In [3]:
from datasets import load_dataset, DatasetDict
from datasets import concatenate_datasets
from IPython.display import HTML

from tqdm import tqdm
import re 
import numpy as np
from markdownify import markdownify as md

In [4]:
ds = load_dataset("HuggingFaceH4/stack-exchange-preferences", split="train", num_proc=16)
ds

Extracting data files: 100%|██████████| 1/1 [00:00<00:00,  2.19it/s]


Dataset parquet downloaded and prepared to /Users/armelzebaze/.cache/huggingface/datasets/HuggingFaceH4___parquet/HuggingFaceH4--stack-exchange-preferences-1d2bff9ecb5ffe2a/0.0.0/2a3b91fbd88a2c90d1dbbb32b460cf621d31bd5b05b934492fdef7d8d6f236ec. Subsequent calls will reuse this data.


Dataset({
    features: ['qid', 'question', 'answers', 'date', 'metadata'],
    num_rows: 10807695
})

In [5]:
HTML(ds[0]["question"])

In [6]:
def lang_callback(el):
    lang = el['class'][0] if el.has_attr('class') else None
    
    if not lang is None:
        lang = lang.split("-")[-1]
    return lang

In [7]:
def html2md(text):
    text = md(text, code_language_callback=lang_callback)
    text = re.sub(r"\n\s*\n", "\n\n", text).strip()
    return text.encode('utf-8', 'replace').decode()

In [8]:
for i in range(1):
    text = html2md(ds[i]["question"])
    print(text)
    print("=="*10)

I have been wanting to learn about 3D printing a long time so I really want this site to succeed but I have no previous experience with the subject. 

I was wondering how can I help the site at this early stage. I thought about asking about how to get started with 3D printing but SE explicitly discourages "easy" questions in the private beta.

What can newbies like me do for the site at this stage besides voting questions and answers?


In [9]:
np.mean([len(ds[i]["answers"])*(len(ds[i]["answers"])-1)/2 for i in range(10000)])

49.935

In [10]:
ds = ds.shuffle(seed=42)
index = list(range(len(ds)))

ds_splits = DatasetDict({
    "finetune": ds.select(index[:3_000_000]),
    "reward": ds.select(index[3_000_000:6_000_000]),
    "rl": ds.select(index[6_000_000:9_000_000]),
    "evaluation": ds.select(index[9_000_000:]),
})

In [11]:
ds_splits

DatasetDict({
    finetune: Dataset({
        features: ['qid', 'question', 'answers', 'date', 'metadata'],
        num_rows: 3000000
    })
    reward: Dataset({
        features: ['qid', 'question', 'answers', 'date', 'metadata'],
        num_rows: 3000000
    })
    rl: Dataset({
        features: ['qid', 'question', 'answers', 'date', 'metadata'],
        num_rows: 3000000
    })
    evaluation: Dataset({
        features: ['qid', 'question', 'answers', 'date', 'metadata'],
        num_rows: 1807695
    })
})

In [48]:
def get_best_answer(answers):
    """return the best answer, that is, the one with the highest score"""
    best_index = 0
    best_score = answers[0]["pm_score"]
    for i in range(1, len(answers)):
        if answers[i]["pm_score"] > best_score :
            best_score = answers[i]["pm_score"]
            best_index = i
    return answers[best_index]["text"]

In [50]:
print(get_best_answer(ds_splits["finetune"][0]["answers"]))

<p>Looking at the library code, seems all events are renamed removing 'fileupload' ... so 'fileuploaddone' becomes just 'done'. It is valid for all other callbacks.
look at this section:</p>

<pre><code>    // Other callbacks:
    // Callback for the submit event of each file upload:
    // submit: function (e, data) {}, // .bind('fileuploadsubmit', func);
    // Callback for the start of each file upload request:
    // send: function (e, data) {}, // .bind('fileuploadsend', func);
    // Callback for successful uploads:
    // done: function (e, data) {}, // .bind('fileuploaddone', func);
    // Callback for failed (abort or error) uploads:
    // fail: function (e, data) {}, // .bind('fileuploadfail', func);
    // Callback for completed (success, abort or error) requests:
    // always: function (e, data) {}, // .bind('fileuploadalways', func);
    // Callback for upload progress events:
    // progress: function (e, data) {}, // .bind('fileuploadprogress', func);
    // Callback f

In [66]:
def preprocess(examples):
    """Cleans HTML and returns the best answer per question."""
    
    n_samples = len(examples["qid"])
    # initialize empty lists for new samples
    new_examples = {"question": [], "response": []}
    for key in examples:
        new_examples[key] = []
        
    for sample_id in range(n_samples):
        # get the best answer among all the answers
        best_answer = get_best_answer(examples["answers"][sample_id])

        # construct the new sample
        for key in examples:
            if key == "question":
                new_examples[key].append(html2md(examples[key][sample_id]))
            else:
                new_examples[key].append(examples[key][sample_id])
        new_examples["response"].append(html2md(best_answer))

    return new_examples

In [68]:
ds_result = ds_splits.map(preprocess, batch_size=1000, batched=True, num_proc=60)

In [69]:
ds_result

DatasetDict({
    finetune: Dataset({
        features: ['qid', 'question', 'answers', 'date', 'metadata', 'response'],
        num_rows: 3000000
    })
    reward: Dataset({
        features: ['qid', 'question', 'answers', 'date', 'metadata', 'response'],
        num_rows: 3000000
    })
    rl: Dataset({
        features: ['qid', 'question', 'answers', 'date', 'metadata', 'response'],
        num_rows: 3000000
    })
    evaluation: Dataset({
        features: ['qid', 'question', 'answers', 'date', 'metadata', 'response'],
        num_rows: 1807695
    })
})

In [70]:
ds_result["finetune"][0]

{'qid': 12891264,
 'question': "I am using jQuery fileupload plugin and I want to do some custom jQuery stuff once fileupload is done\n\nfrom here <https://github.com/blueimp/jQuery-File-Upload/wiki/Options>\n\nNow it says this\n\n```\nCallback for successful upload requests.\n$('#fileupload')\n       .bind('fileuploaddone', function (e, data) {/* ... */})\n\n```\n\nNow I have defined this custom function for testing in my own js file\n\n```\n$('#fileupload').bind('fileuploaddone', function (e, data) {/* ... */\nalert('Hello');\n})\n\n```\n\nBut it's not working.\n\nBut if I edit the main file in here\n\n```\n  // Callback for successful uploads:\n            done: function (e, data) {\n\n```\n\nThen it works.",
 'answers': [{'answer_id': 12891484,
   'author': 'Reflective',
   'author_id': 1686626,
   'author_profile': 'https://Stackoverflow.com/users/1686626',
   'pm_score': 4,
   'selected': True,
   'text': "<p>Looking at the library code, seems all events are renamed removing 'fil

In [71]:
ds_result = ds_result.remove_columns(["answers"])

In [72]:
ds_result

DatasetDict({
    finetune: Dataset({
        features: ['qid', 'question', 'date', 'metadata', 'response'],
        num_rows: 3000000
    })
    reward: Dataset({
        features: ['qid', 'question', 'date', 'metadata', 'response'],
        num_rows: 3000000
    })
    rl: Dataset({
        features: ['qid', 'question', 'date', 'metadata', 'response'],
        num_rows: 3000000
    })
    evaluation: Dataset({
        features: ['qid', 'question', 'date', 'metadata', 'response'],
        num_rows: 1807695
    })
})

In [73]:
for key in ds_result:
    print(key)

finetune
reward
rl
evaluation


In [143]:
import os
import time
from multiprocessing import Pool
from tqdm import tqdm

from huggingface_hub import Repository


def save_shard(shard_tuple):
    """Save shard"""
    filename, shard = shard_tuple
    # use to_json instead to save as json file
    shard.to_parquet(filename)


#def save_manual_shards(ds, user="lvwerra", remote_dataset_repo="stack-exchange-paired", subfolder="train"):
def save_manual_shards(ds, user="ArmelR", remote_dataset_repo="stack-exchange-instruction", subfolder="train"):
    """Save sharded data
    Args:
        ds (Dataset): dataset to be saved
        user (str): user name
        remote_dataset_repo (str): remote dataset repository
        out_path (str): path to save the shards"""
    # this will create a folder OUT_PATH that is a clone of REMOTE_DATASET_REPO
    # you can save the shards inside it and do git add/commit/push to push data to the hub
    out_path = remote_dataset_repo
    # if out path doesnt already exist
    if not os.path.exists(out_path):
        repo = Repository(
            local_dir=out_path,
            clone_from=user + "/" + remote_dataset_repo,
            repo_type="dataset",
            #private=False,
            use_auth_token=True,
            git_user=user,
        )

    # files will be numerous we save them in a folder called data inside out_path
    if not os.path.exists(out_path):
        os.mkdir(out_path + "/data")
    os.mkdir(out_path + f"/data/{subfolder}")
    
    SHARD_SIZE = 1000 << 20
    if ds._indices is not None:
        dataset_nbytes = ds.data.nbytes * len(ds._indices) / len(ds.data)
    else:
        dataset_nbytes = ds.data.nbytes
    num_shards = int(dataset_nbytes / SHARD_SIZE) + 1
    print(f"Number of shards: {num_shards}")

    print("sharding the dataset")
    t_start = time.time()
    shards = (
        ds.shard(num_shards=num_shards, index=i, contiguous=True)
        for i in range(num_shards)
    )
    # use f"{OUT_PATH}/data/train-{index:05d}-of-{num_shards:05d}.json" instead for json files
    filenames = (
        f"{out_path}/data/{subfolder}/train-{index:05d}-of-{num_shards:05d}.parquet"
        for index in range(num_shards)
    )

    with Pool(16) as p:
        list(
            tqdm(
                p.imap_unordered(save_shard, zip(filenames, shards), chunksize=4),
                total=num_shards,
            )
        )
    print(f"Time to save dataset: {time.time()-t_start:.2f}")
    # to push dataset to hub do: git add/commit/push inside OUT_PATH

In [ ]:
for key in ds_result:
    save_manual_shards(ds_result[key], subfolder=key)

In [152]:
#ds_result.push_to_hub("ArmelR/stack-exchange-instruction")

Pushing split finetune to the Hub.
Pushing dataset shards to the dataset hub: 100%|██████████| 14/14 [34:42<00:00, 148.76s/it]
Pushing split reward to the Hub.
Pushing dataset shards to the dataset hub: 100%|██████████| 14/14 [43:54<00:00, 188.17s/it]
Pushing split rl to the Hub.
Pushing dataset shards to the dataset hub: 100%|██████████| 14/14 [45:08<00:00, 193.47s/it]
Pushing split evaluation to the Hub.
Pushing dataset shards to the dataset hub: 100%|██████████| 9/9 [31:37<00:00, 210.87s/it]


In [156]:
#!git clone https://huggingface.co/datasets/ArmelR/stack-exchange-instruction

Cloning into 'stack-exchange-instruction'...
remote: Enumerating objects: 210, done.
remote: Counting objects: 100% (210/210), done.
remote: Compressing objects: 100% (209/209), done.
remote: Total 210 (delta 49), reused 0 (delta 0), pack-reused 0
Receiving objects: 100% (210/210), 26.88 KiB | 8.96 MiB/s, done.
Resolving deltas: 100% (49/49), done.
Filtering content: 100% (51/51), 12.03 GiB | 8.16 MiB/s, done.
